In [2]:
import numpy as np
import pandas as pd
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Dropout
import tensorflow as tf
import matplotlib.pyplot as plt 
import io
import keras.backend as K
from sklearn.preprocessing import RobustScaler, StandardScaler
from sklearn.model_selection import train_test_split, KFold
from sklearn.utils import class_weight


Using TensorFlow backend.


# Import data

In [3]:
# Store the input data in a dataframe
fraud_data = pd.read_csv("creditcard.csv")


# Preprocess data

In [6]:
# shuffle the dataframe so that the inputs are in a random order
df = fraud_data.sample(frac=1).reset_index(drop=True)
#
# Scale the time -1 and 1, since the rest of the features are scaled
robust_scaler = RobustScaler()
scaled_amount = robust_scaler.fit_transform(df['Amount'].values.reshape(-1,1))
scaled_time = robust_scaler.fit_transform(df['Time'].values.reshape(-1,1))
df.drop(['Time','Amount'], axis=1, inplace=True)

# Insert into beginning of df
df.insert(0, 'scaled_amount', scaled_amount)
df.insert(1, 'scaled_time', scaled_time)

# Show the result
df.head()

scaled_amount  scaled_time        V1        V2        V3        V4  \
0       0.614826    -0.464949 -1.031069  0.670519  1.113811 -0.905535   
1       0.530986    -0.333745 -1.322299  1.208908  0.614784  0.620976   
2       0.639838     0.083131  1.773623  0.121835  0.069427  3.942239   
3      -0.167959     0.852900  1.897320 -0.083024 -1.906917  0.076943   
4      -0.293440    -0.163054 -2.115475  0.668166  1.776163 -0.820056   

         V5        V6        V7        V8  ...       V20       V21       V22  \
0 -0.466101 -0.981427  0.501907  0.420606  ... -0.081490  0.020087 -0.380165   
1  0.130962  0.265242  0.633133  0.191222  ... -0.152301  0.157829  0.672778   
2 -0.146466  0.542442 -0.628072  0.164134  ... -0.272968  0.052655  0.166201   
3  1.215640  1.140357 -0.164789  0.376460  ... -0.221257 -0.237919 -0.520314   
4 -0.188667 -1.044734 -0.039221  0.265414  ... -0.409425 -0.077135 -0.501806   

        V23       V24       V25       V26       V27       V28  Class  
0  0.169763  0.533667 -0.443553  0.607723 -0.142564  0.024407      0  
1 -0.056503 -0.291586 -0.271600 -0.351469 -0.329639 -0.081299      0  
2  0.216321  0.590463 -0.363094 -0.075156 -0.046752 -0.023223      0  
3  0.379038 -0.822945 -0.487515  0.267954 -0.015028 -0.053258      0  
4 -0.345225  0.675941 -0.211719  0.602757 -0.558979 -0.136002      0  

[5 rows x 31 columns]

In [ ]:
# Split the data into training (80%) and testing (20%)
train, test = train_test_split(df, test_size=0.2)

# Split data into features and labels
train_features = np.array(train.values[:,:30])
train_labels = np.array(train.values[:,-1])
test_features = np.array(test.values[:,:30])
test_labels = np.array(test.values[:,-1])

print(train_features.shape)
print(test_features.shape)


# Set how much we care about each mis-classification data

In [60]:
# Set How much we value each mis-classification
class_weights = class_weight.compute_class_weight("balanced", np.unique(train_labels), train_labels)


sample_weights=[]

for feature, label in train_features, train_labels:
    if 
        

# Create the model

In [61]:
# Define our custom loss function
def focal_loss(y_true, y_pred):
    gamma = 2.0
    alpha = 0.25
    pt_1 = tf.where(tf.equal(y_true, 1), y_pred, tf.ones_like(y_pred))
    pt_0 = tf.where(tf.equal(y_true, 0), y_pred, tf.zeros_like(y_pred))
    return -K.sum(alpha * K.pow(1. - pt_1, gamma) * K.log(pt_1))-K.sum((1-alpha) * K.pow( pt_0, gamma) * K.log(1. - pt_0))


model = Sequential()

model.add(Dense(units=50, kernel_initializer='uniform', input_dim=train_features.shape[1], activation='relu'))
model.add(Dropout(.2))
model.add(Dense(units=25, kernel_initializer='uniform', activation='relu'))
model.add(Dropout(.2))
model.add(Dense(15, kernel_initializer='uniform', activation='relu'))
model.add(Dense(1, kernel_initializer='uniform', activation='sigmoid'))

# Including the custom loss fxn
model.compile(optimizer='adam', metrics=['accuracy'], loss=[focal_loss])


227845


# Train the model

In [81]:
model.fit(train_features, train_labels, batch_size=50, epochs=25, verbose=1, class_weight=class_weights)



# Get model accuracy 
scores = model.evaluate(test_features, test_labels)
print('\n')
print('accuracy=',scores[1])

# Get predictions from model
output = model.predict_classes(test_features)

# Show confusion matrix
y_actu = pd.Series(test_labels, name='Actual')
y_pred = pd.Series(np.ndarray.flatten(output), name='Predicted')
df_confusion = pd.crosstab(y_actu, y_pred)
print(df_confusion)



num_positives =  (np.count_nonzero(y_actu))
print("True Negative: {}".format(df_confusion[0][0]/y_actu.size))
print("True Positive: {}".format(df_confusion[1][1]/num_positives))
print("False Negative: {}".format(df_confusion[0][1]/y_actu.size))
print("False Positive: {}".format(df_confusion[1][0]/num_positives))

Epoch 1/100
227845/227845 [==============================] - 7s 31us/step - loss: 0.0142 - accuracy: 0.9994
Epoch 2/100
227845/227845 [==============================] - 9s 38us/step - loss: 0.0138 - accuracy: 0.9994
Epoch 3/100
227845/227845 [==============================] - 9s 39us/step - loss: 0.0134 - accuracy: 0.9994
Epoch 4/100
227845/227845 [==============================] - 9s 40us/step - loss: 0.0143 - accuracy: 0.9993
Epoch 5/100
227845/227845 [==============================] - 9s 41us/step - loss: 0.0136 - accuracy: 0.9994
Epoch 6/100
227845/227845 [==============================] - 10s 43us/step - loss: 0.0132 - accuracy: 0.9994
Epoch 7/100
227845/227845 [==============================] - 9s 41us/step - loss: 0.0133 - accuracy: 0.9994
Epoch 8/100
227845/227845 [==============================] - 9s 41us/step - loss: 0.0133 - accuracy: 0.9994
Epoch 9/100
227845/227845 [==============================] - 9s 40us/step - loss: 0.0126 - accuracy: 0.9994
Epoch 10/100
227845/227845 

In [ ]:

    
model.fit(train_features, train_labels, batch_size=50, epochs=25, verbose=1, class_weight=class_weights)



# Get model accuracy 
scores = model.evaluate(test_features, test_labels)
print('\n')
print('accuracy=',scores[1])

# Get predictions from model
output = model.predict_classes(test_features)

# Show confusion matrix
y_actu = pd.Series(test_labels, name='Actual')
y_pred = pd.Series(np.ndarray.flatten(output), name='Predicted')
df_confusion = pd.crosstab(y_actu, y_pred)
print(df_confusion)



num_positives =  (np.count_nonzero(y_actu))
print("True Negative: {}".format(df_confusion[0][0]/y_actu.size))
print("True Positive: {}".format(df_confusion[1][1]/num_positives))
print("False Negative: {}".format(df_confusion[0][1]/y_actu.size))
print("False Positive: {}".format(df_confusion[1][0]/num_positives))